In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F

# 假設有3個類別
num_classes = 3
batch_size = 4

# 模擬模型輸出 (未經softmax)
# 輸出形狀應為 [batch_size, num_classes]
predictions = torch.randn(batch_size, num_classes)

# 模擬真實標籤，假設為one-hot編碼
# 形狀為 [batch_size, num_classes]
targets_one_hot = torch.tensor([
    [1, 0, 0],
    [0, 1, 0],
    [0, 0, 1],
    [0, 1, 0]
], dtype=torch.float32)

# 將one-hot編碼的標籤轉換為類別索引
# 形狀為 [batch_size]
targets = torch.argmax(targets_one_hot, dim=1)

# 定義損失函數
criterion = nn.CrossEntropyLoss()

# 計算損失
loss = criterion(predictions, targets)
print(loss)


tensor(0.8943)


In [2]:
predictions

tensor([[-0.2698,  0.7174, -0.2358],
        [ 1.4976, -1.1554,  3.3826],
        [-0.8067,  1.1254,  1.9788],
        [ 1.3467,  0.7573, -1.5764]])

In [3]:
targets

tensor([0, 1, 2, 1])

In [6]:
print(x for x in range(1, 76))

<generator object <genexpr> at 0x7fd0786385f0>


In [12]:
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
from torchvision import models
import timm


class ModifiedXception(nn.Module):
    def __init__(self, num_classes):
        super(ModifiedXception, self).__init__()
        
        # 加載 Xception 預訓練模型，去掉最後一層 (fc 層)
        self.base_model = timm.create_model(
            'xception', 
            pretrained=True, 
            features_only=True, # 只保留特徵提取部分
            out_indices=[3] # 選擇特徵層索引（根據模型結構）
            )
        
        # 自定義分類頭
        self.custom_head = nn.Sequential(
            nn.AdaptiveAvgPool2d(1),  # Global Average Pooling,
            nn.Flatten(),
            nn.Linear(728, 368),    # Xception 輸出特徵維度為2048
            nn.ReLU(),               # 可選激活函數
            nn.Linear(368, num_classes),
            nn.Sigmoid()
        )

        # self.base_model.fc = nn.Identity()  # 移除原來的 fully connected 層
        
        # # 新增全局平均池化層、隱藏層和輸出層
        # self.global_avg_pool = nn.AdaptiveAvgPool2d(1)  # 全局平均池化
        # self.hidden_layer = nn.Linear(2048, 1370)  # 隱藏層，輸入大小取決於 Xception 的輸出大小
        # self.output_layer = nn.Linear(1370, 2)  # 輸出層，依據分類數目設定
        
        # # 激活函數與 dropout
        # self.relu = nn.ReLU()
        # self.dropout = nn.Dropout(0.6)

    def forward(self, x):
        x = self.base_model(x)               # Xception 主體
        return x


In [13]:
def construct_model():
    '''決定我這次訓練要用哪個model'''
    cnn_model = ModifiedXception(3)

    if torch.cuda.device_count() > 1:
        cnn_model = nn.DataParallel(cnn_model)

    cnn_model = cnn_model.to(torch.device('cuda' if torch.cuda.is_available() else 'cpu'))
    return cnn_model

model = construct_model()
a = model.base_model.feature_info

for b in a:
    print(b)

# last = a[-1]
# last_conv_name = last['module']  # 這通常是 PyTorch Module 的名稱

# last_layer = dict(model.base_model.named_modules()).get(last_conv_name)
# print(f"最後的卷積層: {last_layer}")

# print(last_conv_name)

/opt/conda/lib/python3.11/site-packages/timm/models/_factory.py:126: UserWarning: Mapping deprecated model name xception to current legacy_xception.
  model = create_fn(


{'num_chs': 64, 'reduction': 2, 'module': 'act2', 'index': 0}
{'num_chs': 128, 'reduction': 4, 'module': 'block2.rep.0', 'index': 1}
{'num_chs': 256, 'reduction': 8, 'module': 'block3.rep.0', 'index': 2}
{'num_chs': 728, 'reduction': 16, 'module': 'block12.rep.0', 'index': 3}
{'num_chs': 2048, 'reduction': 32, 'module': 'act4', 'index': 4}


In [ ]:
for c in model.named_modules():
    print(c)

 ModifiedXception(
  (base_model): FeatureHookNet(
    (body): Xception(
      (conv1): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
      (bn1): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (act1): ReLU(inplace=True)
      (conv2): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (act2): ReLU(inplace=True)
      (block1): Block(
        (skip): Conv2d(64, 128, kernel_size=(1, 1), stride=(2, 2), bias=False)
        (skipbn): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (rep): Sequential(
          (0): SeparableConv2d(
            (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), groups=64, bias=False)
            (pointwise): Conv2d(64, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
          )
          (1): BatchNorm2d(128, eps=1e-05, momentum=

In [23]:
model.base_model.body.conv4.pointwise

Conv2d(1536, 2048, kernel_size=(1, 1), stride=(1, 1), bias=False)

In [ ]:
from sklearn.model_selection import KFold

k = KFold(n_splits = 5, shuffle = True)
a = [1, 2, 3, 4 ,5, 6,7, 8]

for d, (b, c) in enumerate(k.split(a)):
    print(d, b, c)

[(array([0, 2, 3, 4, 5, 6]), array([1, 7])), (array([0, 1, 2, 4, 5, 7]), array([3, 6])), (array([0, 1, 3, 4, 6, 7]), array([2, 5])), (array([0, 1, 2, 3, 5, 6, 7]), array([4])), (array([1, 2, 3, 4, 5, 6, 7]), array([0]))]
0 [0 2 3 4 5 6] [1 7]
1 [0 1 3 4 6 7] [2 5]
2 [1 2 4 5 6 7] [0 3]
3 [0 1 2 3 5 6 7] [4]
4 [0 1 2 3 4 5 7] [6]


In [ ]:
from torch.utils.data import Subset, DataLoader, Dataset

class ListDataset(Dataset):
    def __init__(self, data_list, labels_list, status):
        self.data = data_list
        self.labels = labels_list
        self.status = status

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        sample = self.data[idx]  

        if self.status:
            from Image_Process.Image_Generator import Image_generator
            ImageGenerator = Image_generator("", "", 12)
            Transform = ImageGenerator.Generator_Content(5)
            sample = Transform(sample)

        label = self.labels[idx]
        return sample, label

k = KFold(n_splits = 5, shuffle = True)
a = [1, 2, 3, 4 ,5, 6,7, 8]
label = [10, 20, 30, 40, 50,60, 70, 80]

f = ListDataset(a, label, True)

for d, (b, c) in enumerate(k.split(a)):
    # Create training and validation subsets for this fold
    train_subset = torch.utils.data.Subset(training_dataset, train_idx)
    val_subset = torch.utils.data.Subset(training_dataset, val_idx)

